In [12]:
from __future__ import division
import glob
import sys
import os
import pandas as pd
import pybedtools
from pybedtools import BedTool
import errno

In [13]:
#import bedgraph file into dataframe
# cols = ["chr","start", "stop","count?"]
K562_cons_df = pd.read_csv("/Users/jewe1055/experiments/exp45/RUNX1grant/k562_conservative.bed", '\t', header=None) 
Ethan_repA_df = pd.read_csv("/Shares/down/GRO-seq/nextflowhg38_110819_notsenstive/mapped/bedgraphs/Ethan__repA.bedGraph", '\t', header=None) 
Eric_repA_df = pd.read_csv("/Shares/down/GRO-seq/nextflowhg38_110819_notsenstive/mapped/bedgraphs/Eric__repA.bedGraph", '\t', header=None) 

print(K562_cons_df.head())

      0        1        2                     3         4  5
0  chr1  1004968  1005284  chr1:1004968-1005284  18.50630  .
1  chr1  1005178  1005494  chr1:1005178-1005494  10.10933  .
2  chr1  1208931  1209247  chr1:1208931-1209247  29.10315  .
3  chr1  1209152  1209468  chr1:1209152-1209468   6.49805  .
4  chr1  1231851  1232167  chr1:1231851-1232167  37.66789  .


In [43]:
# a = pybedtools.BedTool("/Users/jewe1055/experiments/exp45/RUNX1grant/k562_conservative.bed") 
b = pybedtools.BedTool("/Users/jewe1055/experiments/exp45/output/intersect_count/Ethan_repA.bed")
print(b.count())
# c = pybedtools.BedTool("/Users/jewe1055/experiments/exp45/output/intersect_count/Eric_repA.bed") 
# print((c).count())
# count_runx1peak = (a).count()

# print(count_runx1peak)

68165439


In [21]:

def getann(dir_of_counts="/Users/allenma/RUNX1grant/gene_counts/",suffix=".bed"):
    filenames = os.listdir(dir_of_counts)
    filenames = [filename for filename in filenames if filename.endswith(suffix)]
    frames = []
    filename = filenames[0]
    df = pandas.read_csv(dir_of_counts+filename, sep="\t", names = ["chr", "start", "end", "name", "score", "strand", "thickStart", "thickEnd", "itemRgb", "blockCount", "blockSizes", "blockStarts","counts"])
    ann = df[["chr", "start", "end", "name", "score", "strand", "thickStart", "thickEnd", "itemRgb", "blockCount", "blockSizes", "blockStarts"]]
    return ann


annotation = getann(dir_of_counts="/Users/allenma/RUNX1grant/gene_counts/")
annotation["len"] = annotation["end"]-annotation["start"]


In [21]:

def create_table(dir_of_counts="/Users/allenma/RUNX1grant/gene_counts/", suffix=".bed"):
    filenames = os.listdir(dir_of_counts)
    filenames = [filename for filename in filenames if filename.endswith(suffix)]
    frames = []
    for filename in filenames:
        rootname = filename.split("_counts")[0]
        df = pandas.read_csv(dir_of_counts+filename, sep="\t", names = ["chr", "start", "end", "name", "score", "strand", "thickStart", "thickEnd", "itemRgb", "blockCount", "blockSizes", "blockStarts",rootname])
        frames.append(df[rootname])
    result = pandas.concat(frames, axis=1)
    ann = df[["chr", "start", "end", "name", "score", "strand", "thickStart", "thickEnd", "itemRgb", "blockCount", "blockSizes", "blockStarts"]]
    result["len"] = (ann["end"]-ann["start"])/1000
    return result


def create_table_6bed(dir_of_counts="/Users/allenma/RUNX1grant/gene_counts/", suffix=".bed", minscore=100):
    filenames = os.listdir(dir_of_counts)
    filenames = [filename for filename in filenames if filename.endswith(suffix)]
    frames = []
    for filename in filenames:
        rootname = filename.split("_counts")[0]
        df = pandas.read_csv(dir_of_counts+filename, sep="\t", names = ["chr", "start", "end", "name", "score", "strand",rootname])
        print (df.shape)
        df = df[df["score"]>minscore]
        print (df.shape)
        frames.append(df[rootname])
    result = pandas.concat(frames, axis=1)
    ann = df[["chr", "start", "end", "name", "score", "strand"]]
    result["len"] = (ann["end"]-ann["start"])/1000
    return result


def create_table_4bed(dir_of_counts="/Users/allenma/RUNX1grant/gene_counts/", suffix=".bed"):
    filenames = os.listdir(dir_of_counts)
    filenames = [filename for filename in filenames if filename.endswith(suffix)]
    frames = []
    for filename in filenames:
        rootname = filename.split("_counts")[0]
        df = pandas.read_csv(dir_of_counts+filename, sep="\t", names = ["chr", "start", "end", "name",rootname])
        frames.append(df[rootname])
    result = pandas.concat(frames, axis=1)
    ann = df[["chr", "start", "end", "name"]]
    result["len"] = (ann["end"]-ann["start"])/1000
    return result
                             
df = create_table()





In [7]:



def getmm(filename="/Shares/down/GRO-seq/nextflowhg38_110819_notsenstive/qc/mapstats/Ethan__repA.millionsmapped"):
    f = open(filename)
    l = f.readline()
    l = l.strip("\n")
    l = int(l)
    l = l/1000000
    return l


def calc_fpkm(thisdf,mmdir ="/Shares/down/GRO-seq/nextflowhg38_110819_notsenstive/qc/mapstats/"):
    startcols = thisdf.columns
    startcols = [col for col in startcols if col!="len"]
    fpkmdf = pandas.DataFrame(index=thisdf.index)
    for filename in startcols:
        thismm = getmm(mmdir+filename+".millionsmapped")
        fpkmdf[filename] = thisdf[filename]/(thisdf["len"]*thismm)
    return fpkmdf

    
    
def calc_fpkm2(thisdf,mmdir ="/Shares/down/GRO-seq/nextflowhg38_110819_notsenstive/qc/mapstats/"):
    startcols = thisdf.columns
    thisdf.index = thisdf["name"]
    startcols = [col for col in startcols if col!="len"]
    fpkmdf = pandas.DataFrame(index=thisdf.index)
    for filename in startcols:
        thismm = getmm(mmdir+filename+".millionsmapped")
        fpkmdf[filename] = thisdf[filename]/(thisdf["len"]*thismm)
    return fpkmdf
    

def calc_fpkm3(thisdf,mmdir ="/Shares/down/GRO-seq/nextflowhg38_110819_notsenstive/qc/mapstats/"):
    startcols = thisdf.columns
    thisdf.index = thisdf["name"]
    startcols = [col for col in startcols if col!="len"]
    fpkmdf = pandas.DataFrame(index=thisdf.index)
    for filename in startcols:
        thismm = getmm(mmdir+filename+".millionsmapped")
        fpkmdf[filename] = thisdf[filename]/(thisdf["len"]*thismm)
    return fpkmdf    

fpkmdf = calc_fpkm(df)    

In [8]:

def createtssdf(dir_of_counts="/Users/allenma/RUNX1grant/tss_counts/"):
    df = create_table(dir_of_counts=dir_of_counts)
    fpkmdf = calc_fpkm(df) 
    fpkmdf.to_csv("tss.fpkm")
    return fpkmdf

def createbodydf(dir_of_counts="/Users/allenma/RUNX1grant/body_counts/"):
    df = create_table(dir_of_counts=dir_of_counts)
    fpkmdf = calc_fpkm(df) 
    fpkmdf.to_csv("body.fpkm")
    return fpkmdf

tssdf = createtssdf()
bodydf = createbodydf()

In [12]:
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
#plotly.tools.set_credentials_file(username='maallen3', api_key='mIOiLVHHEqknVnEmvvVg')
init_notebook_mode(connected=False)
import plotly.graph_objs as go
import plotly.figure_factory as ff
import plotly

In [10]:
keep = bodydf[bodydf.mean(axis=1)>0.1].index

In [11]:
tssdf=tssdf[tssdf.index.isin(keep)]
bodydf=bodydf[bodydf.index.isin(keep)]

In [12]:
tssdf2 = pandas.read_csv("/Users/allenma/RUNX1grant/tssvsbody/tss.fpkm.csv", index_col=0)
bodydf2 = pandas.read_csv("/Users/allenma/RUNX1grant/tssvsbody/body.fpkm.csv", index_col=0)

In [1]:


def plottssvsbody(annotation, tssdf, bodydf, col="Ethan__repA"):
    x = tssdf[col]
    y = bodydf[col]
    xy = np.vstack([x,y])
    z = gaussian_kde(xy)(xy)
    fig = go.Figure(data=[go.Scatter(x=x,
        y = y,
        mode='markers',
        hovertext=annotation["name"],
        marker=dict(
            size=10,
            color=z, #set color equal to a variable
            colorscale='Viridis', # one of plotly colorscales
            showscale=True
        )
    )])
    fig.update_layout(xaxis_type="log", yaxis_type="log")
    fig.update_layout(xaxis=dict(title_text="tss fpkm (log)"),yaxis=dict(title_text="body fpkm (log)"), title_text=col)
    plotly.offline.plot(fig, filename = col+'.html', auto_open=False)

In [14]:
plottssvsbody(annotation,tssdf,bodydf)

In [15]:
def createPIdf(annotation, tssdf, bodydf):
    pidf = pandas.DataFrame(index=tssdf.index)
    for col in tssdf.columns:
        pidf[col]=tssdf[col]/bodydf[col]
    return pidf



pidf = createPIdf(annotation, tssdf, bodydf)

In [27]:
ldata = pidf.stack().reset_index(name='value')
ldata = ldata.rename(columns={"level_0":"gene", "level_1":"person", "value":"PI"})

In [28]:
ldata

gene           person        PI
0           0  Elizabeth__repC  1.333949
1           0      Ethan__repB  1.343296
2           0        Eli__repB  0.728620
3           0  Elizabeth__repA  0.811313
4           0      Eli__repBss  0.758985
...       ...              ...       ...
225295  26062        Eli__repC  2.243333
225296  26062       Eric__repA  5.608333
225297  26062      Ethan__repC  4.206250
225298  26062        Eli__repA  5.608333
225299  26062  Elizabeth__repB  1.261875

[225300 rows x 3 columns]

In [29]:
fig = go.Figure()

people = [person for person in sorted(pidf.columns.tolist()) if person.endswith("repA")]

for onepeople in people:
    fig.add_trace(go.Violin(x=ldata['person'][ldata['person'] == onepeople],
                            y=ldata['PI'][ldata['person'] == onepeople],
                            name=onepeople,
                            box_visible=True,
                            meanline_visible=True))
    
fig.update_layout(xaxis=dict(title_text="person"),yaxis=dict(title_text="PI"), title_text="PI distribution")
fig.update_yaxes(range=[-30, 30])

fig.show()


In [30]:
chr21df = annotation[annotation["chr"]=="chr21"]

In [31]:
chr21PI = ldata[ldata["gene"].isin(chr21df.index.tolist())]

In [32]:
fig = go.Figure()

people = [person for person in sorted(pidf.columns.tolist()) if person.endswith("repA")]

for onepeople in people:
    fig.add_trace(go.Violin(x=chr21PI['person'][chr21PI['person'] == onepeople],
                            y=chr21PI['PI'][chr21PI['person'] == onepeople],
                            name=onepeople,
                            box_visible=True,
                            meanline_visible=True))
    
fig.update_layout(xaxis=dict(title_text="person"),yaxis=dict(title_text="PI"), title_text="PI distribution")
fig.update_yaxes(range=[-5, 5])

fig.show()

In [33]:
from scipy import stats
from scipy.stats import norm

fig = go.Figure()

thisdf = ldata

people = [person for person in sorted(pidf.columns.tolist()) if person.endswith("repA")]

print (people)

onepeople="Eric__repA"
personstats = stats.cumfreq(thisdf['PI'][thisdf['person'] == onepeople].tolist(), numbins=500,defaultreallimits=(0, 5))
y = personstats.cumcount
x = np.arange(0,5,personstats.binsize)
fig.add_trace(go.Scatter(x=x, y=y, name="D21"))

onepeople="Ethan__repA"
personstats = stats.cumfreq(thisdf['PI'][thisdf['person'] == onepeople].tolist(), numbins=500,defaultreallimits=(0, 5))
y = personstats.cumcount
x = np.arange(0,5,personstats.binsize)
fig.add_trace(go.Scatter(x=x, y=y, name="T21"))
                
fig.update_layout(font=dict(
        family="Arial",
        size=18
    ),xaxis=dict(title_text="PI"),yaxis=dict(title_text="Genes"), title_text="PI cumulative distribution",plot_bgcolor='rgba(0,0,0,0.03)')

fig.show()

['Eli__repA', 'Elizabeth__repA', 'Eric__repA', 'Ethan__repA']


In [27]:
def createfpkmdf(dir_of_counts="/Users/allenma/RUNX1grant/RUNX1_adult_counts/", outdir = "/Users/allenma/RUNX1grant/",outname="RUNX1_adult.fpkm", minscore=100):
    df = create_table_6bed(dir_of_counts=dir_of_counts, minscore=minscore)
    print (df)
    fpkmdf = calc_fpkm(df) 
    fpkmdf.to_csv(outdir+outname)
    return fpkmdf


def createfpkmdf2(dir_of_counts="/Users/allenma/RUNX1grant/RUNX1_adult_counts/", outdir = "/Users/allenma/RUNX1grant/",outname="RUNX1_adult.fpkm", minscore=100):
    df = create_table_6bed(dir_of_counts=dir_of_counts, minscore=minscore)
    print (df)
    fpkmdf = calc_fpkm2(df) 
    fpkmdf.to_csv(outdir+outname)
    return fpkmdf


def createfpkmdf3(dir_of_counts="/Users/allenma/RUNX1grant/RUNX1_adult_counts/", outdir = "/Users/allenma/RUNX1grant/",outname="RUNX1_adult.fpkm", minscore=100):
    df = create_table_4bed(dir_of_counts=dir_of_counts)
    fpkmdf = calc_fpkm(df) 
    fpkmdf.to_csv(outdir+outname)
    return fpkmdf


#adultRUNX1 = createfpkmdf(dir_of_counts="/Users/allenma/RUNX1grant/RUNX1_adult_counts/", outdir = "/Users/allenma/RUNX1grant/",outname="RUNX1_adult.fpkm")

#fetalRUNX1 = createfpkmdf(dir_of_counts="/Users/allenma/RUNX1grant/RUNX1_fetal_counts/", outdir = "/Users/allenma/RUNX1grant/",outname="RUNX1_fetal.fpkm")

#RUNX1_81223= createfpkmdf(dir_of_counts="/Users/allenma/RUNX1grant/RUNX1_81223/", outdir = "/Users/allenma/RUNX1grant/",outname="RUNX1_81223.fpkm", minscore=100)

#k562_runx_con = createfpkmdf(dir_of_counts="/Users/allenma/RUNX1grant/RUNX1_k562_conser/", outdir = "/Users/allenma/RUNX1grant/",outname="k562_con.fpkm", minscore=0)

#k562_runx_con.index = k562_runx_con.index.tolist()

GABPA = createfpkmdf3(dir_of_counts="/Users/allenma/RUNX1grant/GABPAbindingsites/", outdir = "/Users/allenma/RUNX1grant/",outname="GABPA.fpkm")

GABPA.index = GABPA.index.tolist()



In [28]:
GABPA

Ethan__repC  Elizabeth__repB  Eli__repB  Eric__repA  Eric__repBss  \
0        3.860812         9.820924   9.123225    7.541636     10.185669   
1        1.037934         2.264006   0.387680    2.113757      2.901116   
2        0.506785         0.631674   0.000000    0.412828      1.062380   
3        0.000000         0.000000   0.000000    0.000000      0.000000   
4        0.899543         1.256542   1.042727    0.821207      0.541875   
...           ...              ...        ...         ...           ...   
2176     2.851381         1.015446   1.521463    0.497730      1.138551   
2177     0.000000         0.000000   0.000000    0.000000      0.000000   
2178     0.000000         0.000000   0.000000    0.000000      0.000000   
2179     0.000000         0.000000   0.000000    0.000000      0.000000   
2180     0.000000         0.000000   1.209563    0.000000      0.000000   

      Ethan__repA  Eric__repC  Eric__repB  Eli__repA  Elizabeth__repBss  \
0       12.731207    4.455942    7.833768   9.894755          10.978436   
1        1.324020    1.718004    2.579871   0.389088           0.451937   
2        0.287320    0.209709    0.719803   0.000000           0.220664   
3        0.000000    0.474561    0.000000   0.000000           0.000000   
4        0.747403    0.898496    1.101423   1.046512           2.025924   
...           ...         ...         ...        ...                ...   
2176     1.732051    0.618049    0.289279   1.068890           0.709456   
2177     0.000000    0.000000    0.000000   0.000000           0.000000   
2178     0.000000    0.000000    0.000000   0.000000           0.000000   
2179     0.000000    0.000000    0.000000   0.000000           0.000000   
2180     0.917987    0.670021    0.000000   1.213954           0.000000   

      Elizabeth__repA  Eli__repBss  Eli__repC  Ethan__repBss  Elizabeth__repC  \
0           10.295153    10.489631   3.942857      14.950179         7.094408   
1            1.695236     0.708619   1.215607       1.036526         2.860873   
2            0.496632     0.172996   0.647493       1.301392         0.000000   
3            0.000000     0.000000   0.091578       0.122708         0.316102   
4            1.266555     0.529428   1.089854       1.194813         1.196963   
...               ...          ...        ...            ...              ...   
2176         0.931420     1.390498   2.515451       2.556949         2.694618   
2177         0.000000     0.000000   0.000000       0.000000         0.000000   
2178         0.000000     0.000000   0.000000       0.000000         0.000000   
2179         0.000000     0.000000   0.000000       0.000000         0.000000   
2180         0.000000     1.105446   0.344790       0.153998         0.000000   

      Ethan__repB  
0       13.233195  
1        1.405822  
2        0.549128  
3        0.000000  
4        0.840261  
...           ...  
2176     1.765500  
2177     0.000000  
2178     0.000000  
2179     0.000000  
2180     0.877233  

[2181 rows x 16 columns]

In [35]:
k562_runx_con

Eli__repBss  Eli__repC  Elizabeth__repBss  Elizabeth__repB  Eli__repA  \
0        0.116608   0.945627           0.148739         0.212890   0.128054   
1        0.466433   0.872887           0.446216         0.000000   0.768325   
2        0.466433   1.745774           0.892432         2.128903   0.256108   
3        0.116608   1.673033           0.446216         1.064451   0.256108   
4        0.233216   1.527552           0.297477         0.000000   0.384163   
...           ...        ...                ...              ...        ...   
3145     5.947018   3.564288           3.272252         4.470696   7.042979   
3146     4.431111   3.273325           8.626845         6.173818   5.762438   
3147     0.349825   0.290962           0.000000         0.000000   0.256108   
3148     0.000000   0.072741           0.297477         0.212890   0.000000   
3149     0.116608   0.290962           0.000000         0.425781   0.000000   

      Eric__repB  Ethan__repB  Eric__repBss  Elizabeth__repA  Eric__repC  \
0       0.727775     0.370140      0.238699         0.111585    0.000000   
1       0.485184     0.370140      0.477399         0.111585    0.000000   
2       2.183326     0.740281      1.432196         1.785362    2.214558   
3       2.183326     0.740281      1.432196         1.115851    2.261676   
4       1.455551     0.555211      0.477399         0.334755    1.083720   
...          ...          ...           ...              ...         ...   
3145    5.822204     4.071544      4.773988         4.798160    4.052169   
3146    6.064796     6.477457      4.535288         6.583522    4.523352   
3147    0.000000     0.000000      0.238699         0.000000    0.000000   
3148    0.000000     0.185070      0.000000         0.223170    0.000000   
3149    0.000000     0.000000      0.000000         0.446340    0.047118   

      Ethan__repC  Elizabeth__repC  Eli__repB  Eric__repA  Ethan__repBss  \
0        0.136639         0.000000   0.255182    0.556533       0.194934   
1        0.273279         0.000000   1.020728    0.556533       0.194934   
2        1.298075         0.878783   0.255182    2.504400       0.487336   
3        1.981272         1.255404   0.510364    1.669600       0.584803   
4        0.956476         1.004323   0.255182    1.391333       1.072139   
...           ...              ...        ...         ...            ...   
3145     4.440781         5.649319   6.379552    4.869667       4.970824   
3146     5.465577         5.021617   5.103641    5.426200       6.237897   
3147     0.000000         0.251081   0.510364    0.000000       0.097467   
3148     0.000000         0.000000   0.000000    0.000000       0.000000   
3149     0.000000         0.000000   0.000000    0.000000       0.000000   

      Ethan__repA  
0        0.290502  
1        0.193668  
2        0.871507  
3        0.677839  
4        0.387336  
...           ...  
3145     4.744870  
3146     6.100547  
3147     0.000000  
3148     0.096834  
3149     0.000000  

[3150 rows x 16 columns]

In [29]:
#fetal_ldata = fetalRUNX1.stack().reset_index(name='value')
#fetal_ldata = fetal_ldata.rename(columns={"level_0":"gene", "level_1":"person", "value":"PI"})


#adult_ldata = adultRUNX1.stack().reset_index(name='value')
#adult_ldata = adult_ldata.rename(columns={"level_0":"gene", "level_1":"person", "value":"PI"})

#RUNX1_ldata = RUNX1_81223.stack().reset_index(name='value')
#RUNX1_ldata = RUNX1_ldata.rename(columns={"level_0":"gene", "level_1":"person", "value":"PI"})

GABPA_ldata = GABPA.stack().reset_index(name='value')
GABPA_ldata = GABPA_ldata.rename(columns={"level_0":"gene", "level_1":"person", "value":"PI"})

#k562_runx_con_ldata = k562_runx_con.stack().reset_index(name='value')
#k562_runx_con_ldata = k562_runx_con_ldata.rename(columns={"level_0":"gene", "level_1":"person", "value":"PI"})



In [37]:
from scipy import stats
from scipy.stats import norm

fig = go.Figure()

thisdf = k562_runx_con_ldata

people = [person for person in sorted(pidf.columns.tolist()) if person.endswith("repA")]


for onepeople in people:
    personstats = stats.cumfreq(thisdf['PI'][thisdf['person'] == onepeople].tolist(), numbins=500,defaultreallimits=(0, 10))
    y = personstats.cumcount
    x = np.arange(0,10,personstats.binsize)
    fig.add_trace(go.Scatter(x=x, y=y, name=onepeople))
                
fig.update_layout(xaxis=dict(title_text="fpkm of nascent RNA in lymphoblastiods"),yaxis=dict(title_text="RUNX1 binding sites (in K562)"), title_text="Down sydnrome increases transcription at RUNX1 binding sites")

fig.show()


In [38]:
fig = go.Figure()

thisdf = k562_runx_con_ldata

onepeople="Eric__repA"
personstats = stats.cumfreq(thisdf['PI'][thisdf['person'] == onepeople].tolist(), numbins=30,defaultreallimits=(0, 5))
y = personstats.cumcount
x = np.arange(0,5,personstats.binsize)
fig.add_trace(go.Scatter(x=x, y=y, name="D21"))

onepeople="Ethan__repA"
personstats = stats.cumfreq(thisdf['PI'][thisdf['person'] == onepeople].tolist(), numbins=30,defaultreallimits=(0, 5))
y = personstats.cumcount
x = np.arange(0,5,personstats.binsize)
fig.add_trace(go.Scatter(x=x, y=y, name="T21"))

fig.update_layout(plot_bgcolor='rgba(0,0,0,0.03)',xaxis=dict(title_text="cumfreq of specific fpkm or less in nascent RNA in lymphoblastiods"),yaxis=dict(title_text="RUNX1 binding sites (in K562)"), title_text="Trisomy21 increases transcription over RUNX1 binding sites")

fig.update_layout(font=dict(
        family="Arial",
        size=18
    ))

fig.show()

In [30]:
fig = go.Figure()

thisdf = k562_runx_con_ldata

fpkmmaxs = np.arange(1,5,1)

per_Ethan_fpkms = []
per_Eric_fpkms = []

for fpkmmax in fpkmmaxs:
    total_Ethan =  [fpkm for fpkm in thisdf['PI'][thisdf['person'] == "Ethan__repA"].tolist()]
    total_Eric = [fpkm for fpkm in thisdf['PI'][thisdf['person'] == "Eric__repA"].tolist()]
    above_Ethan = [fpkm for fpkm in thisdf['PI'][thisdf['person'] == "Ethan__repA"].tolist() if fpkm>=fpkmmax]
    above_Eric = [fpkm for fpkm in thisdf['PI'][thisdf['person'] == "Eric__repA"].tolist() if fpkm>=fpkmmax]
    per_Ethan_fpkms.append(len(above_Ethan)/len(total_Ethan))
    per_Eric_fpkms.append(len(above_Eric)/len(total_Eric))
    
    

fig.add_trace(go.Scatter(x=fpkmmaxs, y=per_Eric_fpkms, name="D21",mode="markers",marker_size=20))
fig.add_trace(go.Scatter(x=fpkmmaxs, y=per_Ethan_fpkms, name="T21",mode="markers",marker_size=20))

fig.update_layout(xaxis_type='category', plot_bgcolor='rgba(0,0,0,0.03)',xaxis=dict(title_text="with a fpkm of at least X"),yaxis=dict(title_text="percent of RUNX1 binding sites"), title_text="Transcription at RUNX1 binding sites")

fig.update_layout(font=dict(
        family="Arial",
        size=18
    ))

fig.update_layout(
    autosize=False,
    width=500,
    height=500,
    margin=go.layout.Margin(
        l=50,
        r=50,
        b=100,
        t=100,
        pad=4
    ))

fig.show()

NameError: name 'k562_runx_con_ldata' is not defined

In [14]:
GABPA_ldata

Empty DataFrame
Columns: [gene, person, PI]
Index: []

In [32]:
fig = go.Figure()

thisdf = GABPA_ldata

fpkmmaxs = np.arange(1,5,1)

per_Ethan_fpkms = []
per_Eric_fpkms = []

for fpkmmax in fpkmmaxs:
    total_Ethan =  [fpkm for fpkm in thisdf['PI'][thisdf['person'] == "Ethan__repA"].tolist()]
    total_Eric = [fpkm for fpkm in thisdf['PI'][thisdf['person'] == "Eric__repA"].tolist()]
    above_Ethan = [fpkm for fpkm in thisdf['PI'][thisdf['person'] == "Ethan__repA"].tolist() if fpkm>=fpkmmax]
    above_Eric = [fpkm for fpkm in thisdf['PI'][thisdf['person'] == "Eric__repA"].tolist() if fpkm>=fpkmmax]
    per_Ethan_fpkms.append(len(above_Ethan)/len(total_Ethan))
    per_Eric_fpkms.append(len(above_Eric)/len(total_Eric))
    
    

fig.add_trace(go.Scatter(x=fpkmmaxs, y=per_Eric_fpkms, name="D21",mode="markers",marker_size=20))
fig.add_trace(go.Scatter(x=fpkmmaxs, y=per_Ethan_fpkms, name="T21",mode="markers",marker_size=20))

fig.update_layout(xaxis_type='category', plot_bgcolor='rgba(0,0,0,0.03)',xaxis=dict(title_text="with a fpkm of at least X"),yaxis=dict(title_text="percent of GABPA binding sites"), title_text="Transcription at GABPA binding sites")

fig.update_layout(font=dict(
        family="Arial",
        size=18
    ))

fig.update_layout(
    autosize=False,
    width=500,
    height=500,
    margin=go.layout.Margin(
        l=50,
        r=50,
        b=100,
        t=100,
        pad=4
    ))

fig.show()

In [50]:
fpkmmaxs

array([1, 2, 3, 4])

In [ ]:

df = pandas.read_csv("/Users/allenma/RUNX1grant/"+"81223_PBMCRUNX_hg38.bed", sep="\t", names=["chr", "start", "end", "name", "score"])
df["strand"] ="."
df.to_csv("/Users/allenma/RUNX1grant/"+"81223_PBMCRUNX_hg38.strand.bed", index=False, header=False, sep="\t")


In [ ]:
fig = go.Figure()

thisdf = k562_runx_con_ldata

people = [person for person in sorted(pidf.columns.tolist()) if person.endswith("repC")]

for onepeople in people:
    fig.add_trace(go.Violin(x=thisdf['person'][thisdf['person'] == onepeople],
                            y=thisdf['PI'][thisdf['person'] == onepeople],
                            name=onepeople,
                            box_visible=True,
                            meanline_visible=True))
    
fig.update_layout(xaxis=dict(title_text="person"),yaxis=dict(title_text="PI"), title_text="PI distribution")

fig.update_yaxes(range=[-30, 30])

fig.show()

In [ ]:
RUNX1_81223_fc = pandas.DataFrame(index=RUNX1_81223.index)

RUNX1_81223_fc["fc_Eric_repC_"] = RUNX1_81223["Eric__repC"]/RUNX1_81223["Eli__repC"]
RUNX1_81223_fc["fc_Eric_repBss_"] = RUNX1_81223["Eric__repBss"]/RUNX1_81223["Eli__repBss"]
RUNX1_81223_fc["fc_Eric_repB_"] = RUNX1_81223["Eric__repB"]/RUNX1_81223["Eli__repB"]
RUNX1_81223_fc["fc_Eric_repA_"] = RUNX1_81223["Eric__repA"]/RUNX1_81223["Eli__repA"]

RUNX1_81223_fc["fc_Ethan_repC_"] = RUNX1_81223["Ethan__repC"]/RUNX1_81223["Eli__repC"]
RUNX1_81223_fc["fc_Ethan_repBss_"] = RUNX1_81223["Ethan__repBss"]/RUNX1_81223["Eli__repBss"]
RUNX1_81223_fc["fc_Ethan_repB_"] = RUNX1_81223["Ethan__repB"]/RUNX1_81223["Eli__repB"]
RUNX1_81223_fc["fc_Ethan_repA_"] = RUNX1_81223["Ethan__repA"]/RUNX1_81223["Eli__repA"]

RUNX1_81223_fc = RUNX1_81223_fc.dropna()




In [ ]:
RUNX1_81223_fc_ldata = RUNX1_81223_fc.stack().reset_index(name='value')
RUNX1_81223_fc_ldata = RUNX1_81223_fc_ldata.rename(columns={"level_0":"gene", "level_1":"person", "value":"PI"})


In [ ]:
RUNX1_81223_fc_ldata

In [ ]:
fig = go.Figure()

thisdf = RUNX1_81223_fc_ldata

people = [person for person in sorted(thisdf["person"].unique()) if person.endswith("repC_")]

for onepeople in people:
    fig.add_trace(go.Violin(x=thisdf['person'][thisdf['person'] == onepeople],
                            y=thisdf['PI'][thisdf['person'] == onepeople],
                            name=onepeople,
                            box_visible=True,
                            meanline_visible=True))
    
fig.update_layout(xaxis=dict(title_text="person"),yaxis=dict(title_text="PI"), title_text="PI distribution")

fig.update_yaxes(range=[-30, 30])

fig.show()

In [ ]:

rep="__repA"


Eric = k562_runx_con_ldata[(k562_runx_con_ldata.person=='Eric'+rep)]
Ethan = k562_runx_con_ldata[(k562_runx_con_ldata.person=='Ethan'+rep)]
Eli = k562_runx_con_ldata[(k562_runx_con_ldata.person=='Eli'+rep)]

trace_comp0 = go.Scatter(
    x=Eric["PI"],
    y=Eli["PI"],
    mode='markers',
    marker=dict(size=12,
                line=dict(width=1),
                color="navy"
               ),
    name='typical',
    text=Eli["gene"],
    )

trace_comp1 = go.Scatter(
    x=Ethan["PI"],
    y=Eli["PI"],
    mode='markers',
    marker=dict(size=12,
                line=dict(width=1),
                color="red"
               ),
    name='trisomy',
    text=Eli["gene"],
        )

data_comp = [trace_comp0, trace_comp1]
layout_comp = go.Layout(
    title='Life Expectancy v. Per Capita GDP, 2007',
    hovermode='closest',
    xaxis=dict(
        title='GDP per capita (2000 dollars)',
        ticklen=5,
        zeroline=False,
        gridwidth=2,
    ),
    yaxis=dict(
        title='Life Expectancy (years)',
        ticklen=5,
        gridwidth=2,
    ),
)
fig_comp = go.Figure(data=data_comp, layout=layout_comp)
fig_comp.show()

In [ ]:

rep="__repA"


Eric = k562_runx_con_ldata[(k562_runx_con_ldata.person=='Eric'+rep)]
Ethan = k562_runx_con_ldata[(k562_runx_con_ldata.person=='Ethan'+rep)]
Eli = k562_runx_con_ldata[(k562_runx_con_ldata.person=='Eli'+rep)]

trace_comp0 = go.Scatter(
    x=Eric["PI"],
    y=Ethan["PI"],
    mode='markers',
    marker=dict(size=12,
                line=dict(width=1),
                color="navy"
               ),
    name='typical vs. trisomy',
    text=Eli["gene"],
    )


data_comp = [trace_comp0]
layout_comp = go.Layout(
    title='RUNX1 fpkm',
    hovermode='closest',
    xaxis=dict(
        title='Eric',
        ticklen=5,
        zeroline=False,
        gridwidth=2,
    ),
    yaxis=dict(
        title='Ethan',
        ticklen=5,
        gridwidth=2,
    ),
)

fig_comp = go.Figure(data=data_comp, layout=layout_comp)
fig_comp.update_layout(xaxis_type="log", yaxis_type="log")
fig_comp.show()

In [ ]:
#k562 encode chip (cleanest)

#make6colbed

k562_optimal = pandas.read_csv("/Users/allenma/RUNX1grant/ENCFF091MQJ.bed",sep="\t", names=["chr", "start", "end", "name", "score", "strand", "signalValue", "pValue","qValue","Pointsourcepeak"])


k562_conservative = pandas.read_csv("/Users/allenma/RUNX1grant/ENCFF049YPY.bed", sep="\t", names=["chr", "start", "end", "name", "score", "strand", "signalValue", "pValue","qValue","Pointsourcepeak"])

def fixencodeformat(bedfile="/Users/allenma/RUNX1grant/ENCFF049YPY.bed", outfile="/Users/allenma/RUNX1grant/k562_conservative.bed"):
    bed = pandas.read_csv(bedfile, sep="\t", names=["chr", "start", "end", "name", "score", "strand", "signalValue", "pValue","qValue","Pointsourcepeak"], dtype="str")
    bed["name"] = bed["chr"]+":"+bed["start"]+"-"+bed["end"]
    bed["start"] = bed["start"].astype("int")
    bed["end"] = bed["end"].astype("int")
    bed = bed.sort_values(["chr", "start", "end"])
    bed = bed[["chr", "start", "end", "name", "signalValue", "strand"]]
    bed.to_csv(outfile, header=False, index=False, sep="\t")
    return bed
    
bedout = fixencodeformat(bedfile="/Users/allenma/RUNX1grant/ENCFF049YPY.bed", outfile="/Users/allenma/RUNX1grant/k562_conservative.bed")
bedout = fixencodeformat(bedfile="/Users/allenma/RUNX1grant/ENCFF091MQJ.bed", outfile="/Users/allenma/RUNX1grant/k562_optimal.bed")




In [ ]:

bedout

In [ ]:
k562_runx_con["binding site"] = k562_runx_con.index

In [ ]:
#MAplot 


thisdf = k562_runx_con

person1 = "Ethan"
person2 = "Eric"
rep="__repA"

sample1 = person1+rep
sample2 = person2+rep



MAdf = pandas.DataFrame()
MAdf[sample1] = thisdf[sample1]
MAdf[sample2] = thisdf[sample2]
MAdf["mean"] = MAdf.mean(axis=1)
MAdf = MAdf[MAdf[sample1]!=0]
MAdf = MAdf[MAdf[sample2]!=0]
MAdf["fc"] = MAdf.apply(lambda row: calcfc(row, sample1, sample2), axis=1)
MAdf["binding site"] = MAdf.index.astype("str")

x=MAdf["mean"].tolist()
y=MAdf["fc"].tolist()

trace_comp0 = go.Scatter(
    x=x,
    y=y,
    mode='markers',
    marker=dict(size=4,
               ),
    name='typical vs. trisomy',
    hovertext=MAdf["binding site"].tolist(),hoverinfo="text",)


data_comp = [ trace_comp0]
layout_comp = go.Layout(
    title='RUNX1 fpkm',
    hovermode='closest',
    xaxis=dict(
        title='mean',
        ticklen=5,
        zeroline=False,
        gridwidth=2,
    ),
    yaxis=dict(
        title='fc',
        ticklen=5,
        gridwidth=2,
    ),
)

fig_comp = go.Figure(data=data_comp, layout=layout_comp)
fig_comp.update_layout(xaxis_type="log")
fig_comp.show()



In [ ]:

#MAdf["binding site"] = MAdf.index.astype("str")
MAdf[MAdf["binding site"]=="1679"]

In [ ]:
def calcfc(row, top, bottom):
    if (row[top]/row[bottom])>1:
        return row[top]/row[bottom]
    else:
        valfc = row[bottom]/row[top]
        return -1*valfc
    
    
thisdf = k562_runx_con

person1 = "Ethan"
person2 = "Eric"
person3 = "Eli"
rep="__repC"

sample1 = person1+rep
sample2 = person2+rep
sample3 = person3+rep

    
fcdf = pandas.DataFrame()


fcdf[sample1] = thisdf[sample1]
fcdf[sample2] = thisdf[sample2]
fcdf[sample3] = thisdf[sample3]
fcdf["mean"] = fcdf.mean(axis=1)
fcdf = fcdf[fcdf["mean"]!=0]

fcdf["FC_"+person1] = fcdf.apply(lambda row: calcfc(row, sample1, sample3), axis=1)
fcdf["FC_"+person2] = fcdf.apply(lambda row: calcfc(row, sample2, sample3), axis=1)



fcdf_ldata = fcdf.stack().reset_index(name='value')
fcdf_ldata = fcdf_ldata.rename(columns={"level_0":"gene", "level_1":"person", "value":"PI"})


fig = go.Figure()



people = ["FC_Ethan", "FC_Eric"]
genotype = ["Trisomy", "typical"]

for i, onepeople in enumerate(people):
    fig.add_trace(go.Violin(x=fcdf_ldata['person'][fcdf_ldata['person'] == onepeople],
                            y=fcdf_ldata['PI'][fcdf_ldata['person'] == onepeople],
                            name=genotype[i],
                            box_visible=True,
                            meanline_visible=True))
    
fig.update_layout(xaxis=dict(title_text="person"),yaxis=dict(title_text="Fold change over father"), title_text="PI distribution")

fig.update_yaxes(range=[-30, 30])

fig.show()

In [ ]:
fcdf_ldata

In [26]:
from scipy import stats
from scipy.stats import norm

fig = go.Figure()

thisdf = RUNX1_ldata

people = [person for person in sorted(pidf.columns.tolist()) if person.endswith("repA")]

print (people)

for onepeople in people:
    personstats = stats.cumfreq(thisdf['PI'][thisdf['person'] == onepeople].tolist(), numbins=500,defaultreallimits=(0, 10))
    y = personstats.cumcount
    x = np.arange(0,10,personstats.binsize)
    fig.add_trace(go.Scatter(x=x, y=y, name=onepeople))
                
fig.update_layout(xaxis=dict(title_text="PI"),yaxis=dict(title_text="Genes"), title_text="PI cumulative distribution")

fig.show()

NameError: name 'RUNX1_ldata' is not defined